In [1]:
import pandas as pd
import numpy as np
import geopandas as gpd
import dask.dataframe as dd
from dask.diagnostics import ProgressBar
from datetime import datetime
from matplotlib import pyplot as plt
import warnings
%matplotlib inline
warnings.filterwarnings('ignore')
import emoji
import re
import string
!pip install zhon
from zhon.hanzi import punctuation


In [2]:
df = pd.read_csv('listing_ny_2021_09_filtered_V2.csv')

In [3]:
df.head()

id  availability_30  host_is_superhost  room_type  accommodates  beds  \
0  2595                5                  0          1             1   1.0   
1  3831                0                  0          1             3   3.0   
2  5121               30                  0          1             2   1.0   
3  5136                0                  0          1             4   2.0   
4  5178                1                  0          1             2   1.0   

   price  reviews_per_month  number_of_reviews  review_scores_rating  \
0  150.0               0.33                 48                  4.70   
1   76.0               5.03                408                  4.46   
2   60.0               0.54                 50                  4.52   
3  275.0               0.02                  2                  5.00   
4   68.0               3.64                490                  4.21   

   review_scores_accuracy  review_scores_cleanliness  review_scores_checkin  \
0                    4.72                       4.62                   4.76   
1                    4.59                       4.50                   4.79   
2                    4.22                       4.09                   4.91   
3                    5.00                       5.00                   5.00   
4                    4.20                       3.73                   4.66   

   review_scores_communication  review_scores_location  review_scores_value  \
0                         4.79                    4.86                 4.41   
1                         4.81                    4.72                 4.65   
2                         4.91                    4.47                 4.52   
3                         5.00                    4.50                 5.00   
4                         4.40                    4.86                 4.36   

   instant_bookable                                        description  
0                 0  Beautiful, spacious skylit studio in the heart...  
1                 0  Enjoy 500 s.f. top floor in 1899 brownstone, w...  
2                 0  <b>The space</b><br />HELLO EVERYONE AND THANK...  
3                 0  We welcome you to stay in our lovely 2 br dupl...  
4                 0  Please don’t expect the luxury here just a bas...

In [4]:
from textblob import TextBlob
import nltk
nltk.download('averaged_perceptron_tagger')
nltk.download('punkt')
nltk.download('brown')
nltk.download('wordnet')

[nltk_data] Downloading package averaged_perceptron_tagger to
[nltk_data]     /Users/kaiyuefeng/nltk_data...
[nltk_data]   Package averaged_perceptron_tagger is already up-to-
[nltk_data]       date!
[nltk_data] Downloading package punkt to
[nltk_data]     /Users/kaiyuefeng/nltk_data...
[nltk_data]   Package punkt is already up-to-date!
[nltk_data] Downloading package brown to
[nltk_data]     /Users/kaiyuefeng/nltk_data...
[nltk_data]   Package brown is already up-to-date!
[nltk_data] Downloading package wordnet to
[nltk_data]     /Users/kaiyuefeng/nltk_data...
[nltk_data]   Package wordnet is already up-to-date!


True

In [5]:
def cleantext(data,col):
    data['textcl'] = data[col].str.replace('http\S+|www.\S+', '', case=False)
    data['textcl'] = data['textcl'].str.replace('\B#\S+', '', case=False)
    #data["textcl"] = data['textcl'].str.replace('[^\w\s]','')
    data["textcl"] = data['textcl'].str.replace('\n',' ')
    data['textbcl'] = data['textcl'].str.lower()

In [6]:
cleantext(df,'description')

In [7]:
df.head()

id  availability_30  host_is_superhost  room_type  accommodates  beds  \
0  2595                5                  0          1             1   1.0   
1  3831                0                  0          1             3   3.0   
2  5121               30                  0          1             2   1.0   
3  5136                0                  0          1             4   2.0   
4  5178                1                  0          1             2   1.0   

   price  reviews_per_month  number_of_reviews  review_scores_rating  \
0  150.0               0.33                 48                  4.70   
1   76.0               5.03                408                  4.46   
2   60.0               0.54                 50                  4.52   
3  275.0               0.02                  2                  5.00   
4   68.0               3.64                490                  4.21   

   review_scores_accuracy  review_scores_cleanliness  review_scores_checkin  \
0                    4.72                       4.62                   4.76   
1                    4.59                       4.50                   4.79   
2                    4.22                       4.09                   4.91   
3                    5.00                       5.00                   5.00   
4                    4.20                       3.73                   4.66   

   review_scores_communication  review_scores_location  review_scores_value  \
0                         4.79                    4.86                 4.41   
1                         4.81                    4.72                 4.65   
2                         4.91                    4.47                 4.52   
3                         5.00                    4.50                 5.00   
4                         4.40                    4.86                 4.36   

   instant_bookable                                        description  \
0                 0  Beautiful, spacious skylit studio in the heart...   
1                 0  Enjoy 500 s.f. top floor in 1899 brownstone, w...   
2                 0  <b>The space</b><br />HELLO EVERYONE AND THANK...   
3                 0  We welcome you to stay in our lovely 2 br dupl...   
4                 0  Please don’t expect the luxury here just a bas...   

                                              textcl  \
0  Beautiful, spacious skylit studio in the heart...   
1  Enjoy 500 s.f. top floor in 1899 brownstone, w...   
2  <b>The space</b><br />HELLO EVERYONE AND THANK...   
3  We welcome you to stay in our lovely 2 br dupl...   
4  Please don’t expect the luxury here just a bas...   

                                             textbcl  
0  beautiful, spacious skylit studio in the heart...  
1  enjoy 500 s.f. top floor in 1899 brownstone, w...  
2  <b>the space</b><br />hello everyone and thank...  
3  we welcome you to stay in our lovely 2 br dupl...  
4  please don’t expect the luxury here just a bas...

In [8]:
#df.describe()

In [9]:
a=df['textbcl'].to_string()

In [10]:
a1=string.punctuation
for i in a1:
    m = a.replace(i,'')

In [11]:
for i in punctuation:
    m = m.replace(i,'')

In [12]:
a=emoji.demojize(m)
b=re.sub(':\S+?:', '',a )
c= re.sub('[\u4e00-\u9fa5]','',b)

In [13]:
dfa = TextBlob(c)

In [14]:
token = dfa.words
for w in token:
    print(w)

0
beautiful
spacious
skylit
studio
in
the
heart
1
enjoy
500
s.f
top
floor
in
1899
brownstone
w
2
b
the
space
b
br
hello
everyone
and
thank
3
we
welcome
you
to
stay
in
our
lovely
2
br
dupl
4
please
dont
expect
the
luxury
here
just
a
bas
5
our
best
guests
are
seeking
a
safe
clean
spa
6
beautiful
house
gorgeous
garden
patio
cozy
7
comfortable
studio
apartment
with
super
comfor
8
beautiful
peaceful
healthy
home
br
br
b
9
large
private
loft-like
room
in
a
spacious
2
10
parents/grandparents
coming
to
town
or
are
yo
11
a
true
open-plan
loft
in
a
repurposed
factory
12
b
the
space
b
br
i
am
the
lucky
owner
of
13
hello
please
do
not
hit
request
to
book
h
14
awesome
spacious
clean
1
bedroom
with
a
coz
15
the
room
is
spacious
the
neighborhood
is
safe
16
great
location
br
br
b
the
space
b
br
17
lovely
room
gorgeous
garden
helpful
host
in
18
please
contact
before
sending
reservation
requ
19
b
the
space
b
br
centrally
located
in
the
20
private
room
dedicated
bath
and
a
separate
en
21
super
cute
1
bed

space
b
br
ideal
for
filming
and
ph
249
close
to
columbia
c
park
and
everything
else
250
amazing
2br
loft
on
a
quiet
street
in
the
hear
251
beautiful
1
bedroom
1
bathroom
apartment
righ
252
old
home
with
high
ceilings
with
big
bay
windo
253
you
will
feel
at
ease
and
a
part
of
the
harlem
254
manhattan
's
east
village
is
an
area
rich
multi
255
private
sunny
room
in
the
heart
of
harlem
avai
256
awesome
loft
in
a
great
location
with
easy
sub
257
b
the
space
b
br
hello
my
name
is
fred
258
cute
apartment
in
the
heart
of
williamsburg
i
259
sunlight
pours
through
three
windows
facing
a
260
set
in
a
1800
brownstone
with
original
period
261
private
bedroom
with
twin
bunk
bed
in
spacious
262
great
duplex
apartment
in
the
heart
of
william
263
b
the
space
b
br
one
bdr
apt
with
living
264
newly
renovated
read
our
recent
2019
guests
265
b
the
space
b
br
great
manhattan
apartmen
266
comfortable
spare
room
in
artist
home
the
roo
267
b
the
space
b
br
located
in
very
popular
268
peaceful
comfortable
priv

br
loft
suites
the
box
ho
459
this
loft
unit
features
16ft
ceilings
a
kitch
460
b
the
space
b
br
this
is
a
recently
gut
r
461
this
loft
unit
features
16ft
ceilings
a
kitch
462
b
the
space
b
br
loft
suites
the
box
ho
463
this
loft
unit
features
16ft
ceilings
a
kitch
464
this
loft
unit
features
16ft
ceilings
a
kitch
465
one
sunny
bedroom
available
in
a
three
bedroom
466
best
view
in
nyc
of
central
park
sunrise
eas
467
big
window
lighting
in
quiet
community
near
468
we
have
a
nice
bohemian
little
house
with
2
re
469
b
the
space
b
br
enjoy
my
lovely
sunny
a
470
bathroom
and
kitchen
are
mindfully
shared
with
471
bathroom
and
kitchen
are
mindfully
shared
with
472
this
charming
one
bedroom
apartment
is
central
473
cosy
room
great
location
br
br
b
the
s
474
b
the
space
b
br
large
sunny
inviting
p
475
b
the
space
b
br
experience
new
york
in
t
476
gorgeous
one
bedroom
apartment
sleeps
7
in
c
477
gorgeous
spacious
2
bedroom
apartment
with
fu
478
b
the
space
b
br
fabulous
ues
neighborhoo
479
two-r

b
the
space
b
br
couch
or
clean
cozy
1
b
668
2-story
apartment
with
3
bedrooms
2
renovated
669
b
the
space
b
br
good
size
studio
apartme
670
b
the
space
b
br
charming
williamsburg
ap
671
this
is
a
light-filled
beautiful
apartment
w
672
loft
like
apartment
with
high
ceilings
hard
w
673
b
the
space
b
br
a
garden
floor
level
spa
674
comfortable
queen
side
bed
br
br
b
the
s
675
this
apartment
has
16
windows/doors
on
three
s
676
b
the
space
b
br
i
've
listed
this
apartme
677
beautiful
and
serene
modern
home
with
lots
of
678
very
quiet
big
and
comfortable
studio
in
the
h
679
my
place
is
in
the
historic
harlem
district
ne
680
b
the
space
b
br
i
am
a
wonderful
host
of
681
huge
master
bedroom
is
yours
in
my
beautiful
682
welcome
to
sunny
south
park
slope
br
your
o
683
enjoy
privacy
and
comfort
amongst
midcentury
m
684
we
are
a
professional
couple
and
we
have
an
ex
685
beautiful
charming
brownstone
one
bedroom
90
686
for
rent
in
the
heart
of
greenwich
village
3
687
b
the
space
b
br
when
you
come

beautiful
one
bedroom
i
879
b
the
space
b
br
come
to
manhattan
and
en
880
my
quiet
and
clean
apartment
is
large
and
imma
881
my
cute
cozy
apartment
is
on
a
charming
quiet
882
b
the
space
b
br
apartment
located
only
a
883
it
is
a
very
cozy
and
charming
parlor
floor
ap
884
located
in
a
completely
renovated
landmark
bro
885
confortable
clean
and
cozy
bedroom
near
all
886
b
the
space
b
br
spacious
light
and
airy
887
this
listing
is
for
a
rarely
available
beautif
888
b
the
space
b
br
studio
for
temporary
ren
889
amazing
tree-lined
location
in
the
heart
of
th
890
must
contact
me
before
booking
br
longer
s
891
photo
of
all
guest
is
required
br
br
no
n
892
renting
out
my
apartment
while
i
am
working
ou
893
big
private
room
in
perfect
location
to
explor
894
self-quarantine
in
style
absurdly
clean
rela
895
b
the
space
b
br
in
the
heart
of
the
east
896
wonderful
hip
neighborhood
spacious
apartmen
897
for
shorter
or
longer
stays
feel
free
to
messa
898
our
brooklyn
home
is
a
tranquil
place
to
unwin

...

24984
modern
apartment
in
the
heart
of
bushwick
5
m
24985
5
min
to
walk
br
‣
empire
state
bui
24986
5
min
to
walk
br
‣
empire
state
bui
24987
5
min
to
walk
br
‣
empire
state
bui
24988
welcome
to
new
york
city
br
br
this
is
m
24989
5
min
to
walk
br
‣
empire
state
bui
24990
5
min
to
walk
br
‣
empire
state
bui
24991
5
min
to
walk
br
‣
empire
state
bui
24992
this
boutique
hotel
is
at
an
amazing
location
24993
5
min
to
walk
br
‣
empire
state
bui
24994
5
min
to
walk
br
‣
empire
state
bui
24995
5
min
to
walk
br
‣
empire
state
bui
24996
5
min
to
walk
br
‣
empire
state
bui
24997
enjoy
a
stylish
stay
in
the
heart
of
fort
gree
24998
our
home
is
in
astoria
queens
it
's
a
two
fami
24999
4
bedrooms
1
bath
apartment
each
bedroom
has
25000
modern
apartment
in
the
heart
of
bushwick
5
m
25001
the
apartment
is
on
the
third
floor
of
a
3
sto
25002
this
boutique
hotel
is
at
an
amazing
location
25003
soak
up
the
modern
and
vintage
charm
of
our
co
25004
this
boutique
hotel
is
at
an
amazing
location
25005
soak

of
the
best
l
25252
a
private
bedroom
full-size
bed
in
a
brand
n
25253
three
bedroom
apt
located
in
williamsburg
bro
25254
bright
comfortable
and
clean
room
with
shared
25255
queen
sized
bed
perfect
for
couples
br
br
25256
in
the
amazing
west
village
on
the
beautiful
25257
our
house
is
a
modern
stylish
and
tranquil
be
25258
newly
renovated
loft
in
the
heart
of
bushwick
25259
beautiful
room
with
private
bathroom
clean
q
25260
amazing
renovated
apartment
in
rego
park
br
25261
located
in
a
doorman
building
in
union
square
25262
room
with
a
sofa
bed
and
work
desk
in
owner
's
25263
bright
and
clean
spacious
apartment
privet
r
25264
we
have
few
vans
so
check
their
availability
o
25265
you
will
have
the
whole
studio
apartment
to
yo
25266
hello
welcome
to
my
home
br
i
am
located
25267
brand
new
bright
and
clean
beautiful
two
bedro
25268
private
room
in
beautiful
house
in
queens
loc
25269
located
15
minutes
from
jfk
airport
40
minute
25270
this
is
a
cozy
apartment
in
washington
heights
25271
yo

renovated
3
bd
apt
prospect
lefferts
bk
25517
required
must
be
25
and
have
proof
of
id
br
25518
b
the
space
b
br
the
whole
apartment
unit
25519
roosevelt
parc
creates
a
cocoon
of
serenity
wi
25520
relax
in
out
timeless
european
designed
rooms
25521
this
1-bedroom
is
eccentric
colorful
and
yout
25522
relax
and
enjoy
one
of
the
best
nyc
neighborho
25523
welcome
to
the
big
apple
br
br
enjoy
yo
25524
my
apartment
is
right
in
the
middle
of
everyth
25525
the
map
shows
a
pin
at
w
53rd
st
but
it
is
ac
25526
thank
you
for
your
interest
br
i
am
able
to
25527
take
it
easy
at
this
unique
getaway
brand
new
25528
you
'll
have
a
great
time
at
this
comfortable
p
25529
beautiful
loft
in
brooklyn
right
off
the
ac
tr
25530
no
smoking
no
partying
no
events
or
illegal
25531
enjoy
the
convenience
of
this
bronx
location
n
25532
come
stay
in
this
designer
alternative
to
a
ho
25533
this
place
was
decorated
and
furnished
for
the
25534
amazing
and
beautiful
1
bedroom
apartment
in
t
25535
cute
and
spacious
ground

whistles
a
25784
keep
it
simple
at
this
peaceful
and
centrally
25785
step
into
the
comfort
of
this
stylish
1
br
1
b
25786
whatever
brings
you
to
new
york
city
stay
rig
25787
spacious
sun
drenched
room
with
blackout
curta
25788
a
private
room
in
a
shared
apartment
located
i
25789
la
sienna
is
a
guesthouse
located
in
west
harl
25790
beautiful
bright
single
room
25791
peaceful
family
oriented
area
and
guests
with
25792
the
crown
retreat
lll
br
is
a
2br
queen
size
25793
keep
it
simple
at
this
peaceful
and
centrally
25794
3-br
on
2nd
floor
of
home
br
front
back
b
25795
the
apartment
br
br
one
bedroom
apartment
25796
beautiful
and
cozy
1
bed
room
apt
in
the
heart
25797
located
in
a
brick
townhouse
built
in
1910
th
25798
kick
back
and
relax
in
this
calm
boho
stylis
25799
the
apt
is
in
brooklyn
near
the
ocean
very
25800
kick
back
and
relax
in
this
calm
stylish
spac
25801
5
min
to
walk
br
‣
empire
state
bui
25802
a
one
of
a
kind
great
studio
in
the
heart
of
n
25803
newly
renovated
modern
studio

there
is
a
2
26074
hello
welcome
to
my
home
you
will
be
renting
26075
420
friendly
comfortable
spacious
three
bed
26076
pls
send
a
msg
before
sending
a
booking
requ
26077
no
smoking/parties/loud
music/extra
visitors
b
26078
room
in
flushing
queens
with
a
lot
of
space
fo
26079
a
cozy
1
bedroom
apartment
with
kitchen
and
ba
26080
come
unwind
and
relax
in
this
fresh
and
cozy
26081
enjoy
a
tranquil
experience
at
a
prime
astoria
26082
enjoy
a
stylish
experience
at
this
chic
centr
26083
perfect
summer
rental
true
2
bedroom
in
prime
26084
the
house
is
renovated
and
it
's
being
newly
fu
26085
amazing
and
comfortable
space
in
brooklyn
sam
26086
amazing
and
comfortable
space
in
brooklyn
sam
26087
queit
room
in
peaceful
nyc
neighborhood
26088
welcome
to
harlem
this
is
the
biggest
apartme
26089
this
stylish
place
to
stay
is
perfect
for
coup
26090
your
family
will
be
close
to
everything
when
y
26091
dont
stay
in
a
hotel
come
hang
out
in
brookl
26092
spacious
bronx
apartment
with
storage
space
a
260

In [15]:
dfa.tags

[('0', 'CD'),
 ('beautiful', 'JJ'),
 ('spacious', 'JJ'),
 ('skylit', 'NN'),
 ('studio', 'NN'),
 ('in', 'IN'),
 ('the', 'DT'),
 ('heart', 'NN'),
 ('1', 'CD'),
 ('enjoy', 'NN'),
 ('500', 'CD'),
 ('s.f', 'NN'),
 ('top', 'JJ'),
 ('floor', 'NN'),
 ('in', 'IN'),
 ('1899', 'CD'),
 ('brownstone', 'NN'),
 ('w', 'NN'),
 ('2', 'CD'),
 ('<', 'NN'),
 ('b', 'NN'),
 ('>', 'IN'),
 ('the', 'DT'),
 ('space', 'NN'),
 ('<', 'NNP'),
 ('/b', 'NNP'),
 ('>', 'NNP'),
 ('<', 'NNP'),
 ('br', 'NN'),
 ('/', 'NNP'),
 ('>', 'NNP'),
 ('hello', 'VBD'),
 ('everyone', 'NN'),
 ('and', 'CC'),
 ('thank', 'NN'),
 ('3', 'CD'),
 ('we', 'PRP'),
 ('welcome', 'VBP'),
 ('you', 'PRP'),
 ('to', 'TO'),
 ('stay', 'VB'),
 ('in', 'IN'),
 ('our', 'PRP$'),
 ('lovely', 'JJ'),
 ('2', 'CD'),
 ('br', 'NN'),
 ('dupl', 'NN'),
 ('4', 'CD'),
 ('please', 'NN'),
 ('dont', 'NN'),
 ('expect', 'VBP'),
 ('the', 'DT'),
 ('luxury', 'NN'),
 ('here', 'RB'),
 ('just', 'RB'),
 ('a', 'DT'),
 ('bas', 'NN'),
 ('5', 'CD'),
 ('our', 'PRP$'),
 ('best', 'JJS'),
 (

In [16]:
from pandas.core.frame import DataFrame
df3 =DataFrame(dfa.tags)

In [17]:
df3

0   1
0               0  CD
1       beautiful  JJ
2        spacious  JJ
3          skylit  NN
4          studio  NN
...           ...  ..
252926       area  NN
252927       with  IN
252928        the  DT
252929    coolest  NN
252930          h  NN

[252931 rows x 2 columns]

In [18]:
df3.head()

0   1
0          0  CD
1  beautiful  JJ
2   spacious  JJ
3     skylit  NN
4     studio  NN

In [19]:
df3.columns=['words','tags']

In [20]:
c=df3.loc[df3['words']=='covid']
c

words tags
596     covid   NN
1260    covid   NN
9530    covid   NN
10520   covid   JJ
14838   covid   NN
20822   covid   NN
34733   covid   JJ
36035   covid   VB
41158   covid   NN
46304   covid   VB
54449   covid   JJ
60512   covid   NN
63077   covid   JJ
68850   covid   NN
102540  covid   NN
111172  covid   NN
120645  covid   VB
122339  covid   JJ
140744  covid   VB
147428  covid   VB
148912  covid   JJ
152048  covid   JJ
157492  covid   JJ
165181  covid   JJ
167834  covid   JJ
173813  covid   NN
176682  covid   NN
178255  covid   NN
180353  covid   NN
187310  covid   VB
195638  covid   JJ
211252  covid   NN
219578  covid   NN
226462  covid   NN

In [21]:
#d= c.groupby(['tags']).agg({'words':'count'})

In [22]:
a=df3.groupby(['words','tags']).agg({'tags':'count'})

In [23]:
a

tags
words     tags      
%         NN      15
&         CC     577
'         POS     35
'best     JJS      1
'brooklyn CD       1
...              ...
𝘾𝙄𝙏𝙔      NNP      1
𝙉𝙀𝙒       NNP      1
𝙏𝙊        NNP      1
𝙒𝙀𝙇𝘾𝙊𝙈𝙀   JJ       1
𝙔𝙊𝙍𝙆      NNP      1

[37540 rows x 1 columns]

In [24]:
#a= a.loc[a['tags']>1]

In [25]:
a=a.drop(a.tail(136).index)

In [26]:
a.tail(30)

tags
words       tags      
yearly      RB       1
yearning    NN       1
years       NNS     26
yellow      JJ       2
yes         NNS      1
            RB       1
            UH       3
yet         RB      35
yo          NN      36
            NNS      8
            VB       1
yoga        NN       1
yolo        NN       1
yor         NN       6
york        JJ       9
            NN     387
            NNP      4
york-lower  NN       1
york.       NN       1
york/       NN       1
yorke       NN       1
yorker      NN      29
yorkishhhhh NN       1
yorks       NNS      5
yorkville   NN       3
yotam       JJ       1
you         PRP    942
you.        JJ       1
you.we      VB       1
youl        NN       1

In [27]:
#a=a.drop(a.tail(50).index)
#a.tail(60)

In [28]:
df3

words tags
0               0   CD
1       beautiful   JJ
2        spacious   JJ
3          skylit   NN
4          studio   NN
...           ...  ...
252926       area   NN
252927       with   IN
252928        the   DT
252929    coolest   NN
252930          h   NN

[252931 rows x 2 columns]

In [29]:
#CD,

In [30]:
df3.tags.unique()

array(['CD', 'JJ', 'NN', 'IN', 'DT', 'NNP', 'VBD', 'CC', 'PRP', 'VBP',
       'TO', 'VB', 'PRP$', 'RB', 'JJS', 'NNS', 'VBG', 'VBZ', 'VBN', 'WP',
       'PDT', 'RBR', 'RP', 'WDT', 'JJR', 'MD', 'WRB', 'POS', 'EX', 'RBS',
       'FW', 'UH', 'SYM'], dtype=object)

In [31]:
df4=df3.loc[df3['tags'].isin(['JJ','NN','VBD','VB','VBP','RB','JJS','NNS','VBG','VBZ','VBN','JJR','RBS','RBR','RP','NNP'])]

In [32]:
g= df4.groupby(['words']).agg({'tags':'count'})

In [33]:
g

tags
words        
%          15
'best       1
'burg       1
'in         1
'm        109
...       ...
𝘾𝙄𝙏𝙔        1
𝙉𝙀𝙒         1
𝙏𝙊          1
𝙒𝙀𝙇𝘾𝙊𝙈𝙀     1
𝙔𝙊𝙍𝙆        1

[7971 rows x 1 columns]

In [34]:
g['tags'].sum()

155573

In [35]:
g['frequency']=g['tags']/198250

In [36]:
g.sort_values(by='frequency',ascending=False).head(200)

tags  frequency
words                      
apartment   5982   0.030174
is          5401   0.027243
bedroom     4505   0.022724
<           4273   0.021554
>           3231   0.016298
...          ...        ...
level        123   0.000620
read         123   0.000620
convenient   123   0.000620
good         120   0.000605
wi           120   0.000605

[200 rows x 2 columns]

In [48]:
g.to_csv('ml2021.csv')

In [49]:
ml2018=pd.read_csv('ml_2018.csv')

In [50]:
growth = g.merge(ml2018,left_on='words',right_on='words',how='left')

In [51]:
growth

words  tags_x  frequency_x  tags_y  \
0                                        %      15     0.000076    19.0   
1                                    'best       1     0.000005     1.0   
2                                    'burg       1     0.000005     1.0   
3                                      'in       1     0.000005     1.0   
4                                       'm     109     0.000550   232.0   
5                                    'park       1     0.000005     1.0   
6                                 'premium       1     0.000005     NaN   
7                                      're      84     0.000424   126.0   
8                                       's     194     0.000979   329.0   
9                                   'south       1     0.000005     NaN   
10                                    'the       3     0.000015     1.0   
11                                   'unic       1     0.000005     NaN   
12                                     've      33     0.000166    85.0   
13                                  'white       2     0.000010     2.0   
14                                       *     789     0.003980   860.0   
15                                       +      44     0.000222    89.0   
16                                      +1       1     0.000005     1.0   
17                              +beautiful       1     0.000005     NaN   
18                                +private       1     0.000005     1.0   
19                                     ,,2       1     0.000005     1.0   
20                                      ,3       2     0.000010     1.0   
21                                      ,8       1     0.000005     NaN   
22                                  ,8,207       3     0.000015     3.0   
23                                      -1       2     0.000010     1.0   
24                                     -10       2     0.000010     NaN   
25                                     -15       2     0.000010     1.0   
26                                     -19       2     0.000010     NaN   
27                                    -1bd       1     0.000005     NaN   
28                                      -2       4     0.000020     4.0   
29                                     -20       1     0.000005     1.0   
30                                      -5       1     0.000005     1.0   
31                                    -a/c       1     0.000005     NaN   
32                                    -air       1     0.000005     NaN   
33                                     -an       1     0.000005     NaN   
34                              -apartment       2     0.000010     1.0   
35                              -available       1     0.000005     1.0   
36                              -beautiful       2     0.000010     3.0   
37                                    -big       1     0.000005     2.0   
38                                 -bright       1     0.000005     NaN   
39                             -christophe       1     0.000005     1.0   
40                                  -clean       1     0.000005     2.0   
41                            -comfortably       1     0.000005     NaN   
42                                   -cute       2     0.000010     NaN   
43                             -discretion       1     0.000005     NaN   
44                                  -fully       4     0.000020     3.0   
45                                  -great       2     0.000010     2.0   
46                                    -gym      14     0.000071    20.0   
47                                      -h       1     0.000005     NaN   
48                               -hardwood       1     0.000005     1.0   
49                                  -large       1     0.000005     2.0   
50                                -located       1     0.000005     1.0   
51                                      -m       1     0.000005     1.0   
52                                   -mask       1     0.00000

In [52]:
growth=growth.fillna(0)

In [53]:
growth['growth']=growth['frequency_x']-growth['frequency_y']

In [54]:
b=growth.loc[growth['words']=='hospital']

In [55]:
b

words  tags_x  frequency_x  tags_y  frequency_y   growth
3603  hospital      13     0.000066     5.0     0.000025  0.00004

In [56]:
growth.sort_values(by='growth',ascending=False).head(50)

words  tags_x  frequency_x  tags_y  frequency_y    growth
284                    <    4273     0.021554     3.0     0.000015  0.021538
286                    >    3231     0.016298    12.0     0.000061  0.016237
1210                  br    2970     0.014981   403.0     0.002033  0.012948
99                     /    2633     0.013281   150.0     0.000757  0.012525
102                   /b     637     0.003213     0.0     0.000000  0.003213
790                    b    1146     0.005781   584.0     0.002946  0.002835
6504               space    1178     0.005942   826.0     0.004166  0.001776
5810               relax     199     0.001004    91.0     0.000459  0.000545
7059            timeless      99     0.000499     3.0     0.000015  0.000484
2643            european      98     0.000494     3.0     0.000015  0.000479
6048               rooms     220     0.001110   145.0     0.000731  0.000378
2202            designed     182     0.000918   114.0     0.000575  0.000343
1781  community-oriented      62     0.000313     0.0     0.000000  0.000313
6277          sharedeasy      52     0.000262     0.0     0.000000  0.000262
1976            covid-19      51     0.000257     0.0     0.000000  0.000257
7797            woodside      51     0.000257     5.0     0.000025  0.000232
6767                 sty      52     0.000262     6.0     0.000030  0.000232
383                  adj      41     0.000207     0.0     0.000000  0.000207
485                alley      40     0.000202     0.0     0.000000  0.000202
7350            untitled      40     0.000202     0.0     0.000000  0.000202
3025             freeman      40     0.000202     0.0     0.000000  0.000202
6626               start      43     0.000217     8.0     0.000040  0.000177
7330                uniq      37     0.000187     2.0     0.000010  0.000177
3554        historically      38     0.000192     3.0     0.000015  0.000177
1718                coli      35     0.000177     0.0     0.000000  0.000177
5554      professionally      46     0.000232    12.0     0.000061  0.000172
1663            cleaning      39     0.000197     5.0     0.000025  0.000172
1973               covid      34     0.000172     0.0     0.000000  0.000172
591           apartment.      32     0.000161     0.0     0.000000  0.000161
1206              bowery      43     0.000217    12.0     0.000061  0.000156
7426          vaccinated      30     0.000151     0.0     0.000000  0.000151
4426                manh      54     0.000272    25.0     0.000126  0.000146
1450               cassa      29     0.000146     0.0     0.000000  0.000146
5650             queens.      27     0.000136     0.0     0.000000  0.000136
1656             cleaned      32     0.000161     5.0     0.000025  0.000136
5114                 out     177     0.000893   151.0     0.000762  0.000131
6922                take      65     0.000328    39.0     0.000197  0.000131
3558                  ho      62     0.000313    37.0     0.000187  0.000126
4424             managed      28     0.000141     3.0     0.000015  0.000126
1285           brooklyns      31     0.000156     6.0     0.000030  0.000126
1204            boutique      66     0.000333    42.0     0.000212  0.000121
6503                spac      59     0.000298    35.0     0.000177  0.000121
3977                kick      29     0.000146     5.0     0.000025  0.000121
3888             jackson      36     0.000182    13.0     0.000066  0.000116
7226             trusted      23     0.000116     0.0     0.000000  0.000116
1935           corporate      29     0.000146     6.0     0.000030  0.000116
7336                unit     137     0.000691   115.0     0.000580  0.000111
7833                   y     100     0.000504    78.0     0.000393  0.000111
6751             studios      31     0.000156     9.0     0.000045  0.000111
6130                 sce      23     0.000116     1.0     0.000005  0.000111

In [57]:
pd.set_option('display.max_row', None)

In [58]:
growth.sort_values(by='growth',ascending=False).head(300)

words  tags_x  frequency_x  tags_y  frequency_y    growth
284                    <    4273     0.021554     3.0     0.000015  0.021538
286                    >    3231     0.016298    12.0     0.000061  0.016237
1210                  br    2970     0.014981   403.0     0.002033  0.012948
99                     /    2633     0.013281   150.0     0.000757  0.012525
102                   /b     637     0.003213     0.0     0.000000  0.003213
790                    b    1146     0.005781   584.0     0.002946  0.002835
6504               space    1178     0.005942   826.0     0.004166  0.001776
5810               relax     199     0.001004    91.0     0.000459  0.000545
7059            timeless      99     0.000499     3.0     0.000015  0.000484
2643            european      98     0.000494     3.0     0.000015  0.000479
6048               rooms     220     0.001110   145.0     0.000731  0.000378
2202            designed     182     0.000918   114.0     0.000575  0.000343
1781  community-oriented      62     0.000313     0.0     0.000000  0.000313
6277          sharedeasy      52     0.000262     0.0     0.000000  0.000262
1976            covid-19      51     0.000257     0.0     0.000000  0.000257
7797            woodside      51     0.000257     5.0     0.000025  0.000232
6767                 sty      52     0.000262     6.0     0.000030  0.000232
383                  adj      41     0.000207     0.0     0.000000  0.000207
485                alley      40     0.000202     0.0     0.000000  0.000202
7350            untitled      40     0.000202     0.0     0.000000  0.000202
3025             freeman      40     0.000202     0.0     0.000000  0.000202
6626               start      43     0.000217     8.0     0.000040  0.000177
7330                uniq      37     0.000187     2.0     0.000010  0.000177
3554        historically      38     0.000192     3.0     0.000015  0.000177
1718                coli      35     0.000177     0.0     0.000000  0.000177
5554      professionally      46     0.000232    12.0     0.000061  0.000172
1663            cleaning      39     0.000197     5.0     0.000025  0.000172
1973               covid      34     0.000172     0.0     0.000000  0.000172
591           apartment.      32     0.000161     0.0     0.000000  0.000161
1206              bowery      43     0.000217    12.0     0.000061  0.000156
7426          vaccinated      30     0.000151     0.0     0.000000  0.000151
4426                manh      54     0.000272    25.0     0.000126  0.000146
1450               cassa      29     0.000146     0.0     0.000000  0.000146
5650             queens.      27     0.000136     0.0     0.000000  0.000136
1656             cleaned      32     0.000161     5.0     0.000025  0.000136
5114                 out     177     0.000893   151.0     0.000762  0.000131
6922                take      65     0.000328    39.0     0.000197  0.000131
3558                  ho      62     0.000313    37.0     0.000187  0.000126
4424             managed      28     0.000141     3.0     0.000015  0.000126
1285           brooklyns      31     0.000156     6.0     0.000030  0.000126
1204            boutique      66     0.000333    42.0     0.000212  0.000121
6503                spac      59     0.000298    35.0     0.000177  0.000121
3977                kick      29     0.000146     5.0     0.000025  0.000121
3888             jackson      36     0.000182    13.0     0.000066  0.000116
7226             trusted      23     0.000116     0.0     0.000000  0.000116
1935           corporate      29     0.000146     6.0     0.000030  0.000116
7336                unit     137     0.000691   115.0     0.000580  0.000111
7833                   y     100     0.000504    78.0     0.000393  0.000111
6751             studios      31     0.000156     9.0     0.000045  0.000111
6130                 sce      23     0.000116     1.0     0.000005  0.000111
5589              provid      22     0.000111     0.0     0.000000  0.000111
4243           